In [18]:
import pandas as pd
import numpy as np
import os
import sumolib
import random
from tqdm import tqdm
from datetime import datetime

In [19]:
# plan_original = pd.read_csv('../../Data/tables/plan_original.csv', index_col=0)
# plan_original_ = plan_original[plan_original.start_hour==0]
# # plan_original_ = plan_original_[plan_original_.inter_no.isin([175, 210])]
# with pd.option_context('display.max_rows', None, 'display.max_columns', None):
#     display(plan_original_) # overlap : 175, 201, 210

# 1. 이동류 매칭

In [20]:
# [이동류번호] 불러오기
path_moves = '../../Data/tables/moves/'
csv_moves = os.listdir('../../Data/tables/moves/')
moves = [pd.read_csv(path_moves + csv_move, index_col=0) for csv_move in tqdm(csv_moves)]
match1 = pd.concat(moves).drop_duplicates().sort_values(by=['inter_no','phas_A','phas_B']).reset_index(drop=True)
match1 = match1[match1.inter_no!=212]
match1.head(10)

  0%|          | 0/17280 [00:00<?, ?it/s]

100%|██████████| 17280/17280 [00:55<00:00, 310.34it/s]


inter_no  phas_A  phas_B  move_A  move_B
0       175       1       1       8       4
1       175       2       2       7       3
2       175       3       3       6       1
3       175       3       4       6       2
4       175       4       4       5       2
5       176       1       1       8       4
6       176       2       2       8       3
7       176       3       3       5      18
8       177       1       1       8       4
9       177       2       2       7       3

In [21]:
# 계층화
moveA = match1[['inter_no', 'phas_A', 'move_A']].copy()
moveA.columns = ['inter_no', 'phase_no', 'move_no']
moveA['ring_type'] = 'A'
moveB = match1[['inter_no', 'phas_B', 'move_B']].copy()
moveB.columns = ['inter_no', 'phase_no', 'move_no']
moveB['ring_type'] = 'B'
match2 = pd.concat([moveA, moveB]).drop_duplicates()
match2 = match2[['inter_no', 'phase_no', 'ring_type', 'move_no']]
match2 = match2.sort_values(by=list(match2.columns))
match2.head(10)

inter_no  phase_no ring_type  move_no
0       175         1         A        8
0       175         1         B        4
1       175         2         A        7
1       175         2         B        3
2       175         3         A        6
2       175         3         B        1
4       175         4         A        5
3       175         4         B        2
5       176         1         A        8
5       176         1         B        4

In [22]:
# [nema 이동류목록] 불러오기 및 병합
nema = pd.read_csv('../../Data/tables/nema.csv', encoding='cp949')
match3 = pd.merge(match2, nema, how='left', left_on='move_no', right_on='이동류번호').drop_duplicates()
match3.rename(columns={'진입방향': 'inc_dir', '진출방향': 'out_dir'}, inplace=True)
match3.drop('이동류번호', axis=1, inplace=True)
match3

inter_no  phase_no ring_type  move_no inc_dir out_dir
0        175         1         A        8       남       북
1        175         1         B        4       북       남
2        175         2         A        7       북       동
3        175         2         B        3       남       서
4        175         3         A        6       동       서
..       ...       ...       ...      ...     ...     ...
59       210         4         B        3       남       서
60       211         1         A        6       동       서
61       211         1         B        2       서       동
62       211         2         A       17     NaN     NaN
63       211         2         B       18     NaN     NaN

[64 rows x 6 columns]

In [23]:
# [방위각정보] 불러오기 및 병합
angle = pd.read_csv('../../Data/tables/angle.csv', index_col=0)
six_chars = angle.angle_code.apply(lambda x:len(x)==6)
angle.loc[six_chars,'inc_angle'] = angle.angle_code.apply(lambda x:x[:3])
angle.loc[six_chars,'out_angle'] = angle.angle_code.apply(lambda x:x[3:])
angle = angle.drop('angle_code', axis=1)
match4 = pd.merge(match3, angle, how='left', left_on=['inter_no', 'phase_no', 'ring_type'],
                 right_on=['inter_no', 'phase_no', 'ring_type']).drop_duplicates()
match4

inter_no  phase_no ring_type  move_no inc_dir out_dir inc_angle out_angle
0        175         1         A        8       남       북       179       004
1        175         1         B        4       북       남       NaN       NaN
2        175         2         A        7       북       동       NaN       NaN
3        175         2         B        3       남       서       179       270
4        175         3         A        6       동       서       NaN       NaN
..       ...       ...       ...      ...     ...     ...       ...       ...
59       210         4         B        3       남       서       180       270
60       211         1         A        6       동       서       NaN       NaN
61       211         1         B        2       서       동       270       090
62       211         2         A       17     NaN     NaN       NaN       NaN
63       211         2         B       18     NaN     NaN       NaN       NaN

[64 rows x 8 columns]

In [24]:
# [네트워크], [교차로-노드 매칭], [교차로정보] 불러오기 
net = sumolib.net.readNet('../../Data/networks/SN_sample.net.xml')
inter_node = pd.read_csv('../../Data/tables/inter_node.csv', index_col=0)
inter_info = pd.read_csv('../../Data/tables/inter_info.csv', index_col=0)

inter_node1 = inter_node[inter_node.inter_type == 'parent'].drop('inter_type', axis=1)
inter_info1 = inter_info[['inter_no', 'inter_lat', 'inter_lon']]
inter = pd.merge(inter_node1, inter_info1, how='left', left_on=['inter_no'],
                 right_on=['inter_no']).drop_duplicates()

inter2node = dict(zip(inter['inter_no'], inter['node_id']))

match5 = match4.copy()
# 진입진출ID 매칭
for index, row in match5.iterrows():
    node_id = inter2node[row.inter_no]
    node = net.getNode(node_id)
    # 교차로의 모든 (from / to) edges
    inc_edges = [edge for edge in node.getIncoming() if edge.getFunction() == ''] # incoming edges
    out_edges = [edge for edge in node.getOutgoing() if edge.getFunction() == ''] # outgoing edges
    # 교차로의 모든 (from / to) directions
    inc_dirs = []
    for inc_edge in inc_edges:
        start = inc_edge.getShape()[-2]
        end = inc_edge.getShape()[-1]
        inc_dir = np.array(end) - np.array(start)
        inc_dir = inc_dir / (inc_dir ** 2).sum() ** 0.5
        inc_dirs.append(inc_dir)
    out_dirs = []
    for out_edge in out_edges:
        start = out_edge.getShape()[0]
        end = out_edge.getShape()[1]
        out_dir = np.array(end) - np.array(start)
        out_dir = out_dir / (out_dir ** 2).sum() ** 0.5
        out_dirs.append(out_dir)
    # 진입각, 진출각 불러오기
    if not pd.isna(row.inc_angle):
        inc_angle = int(row.inc_angle)
        out_angle = int(row.out_angle)
        # 방위각을 일반각으로 가공, 라디안 변환, 단위벡터로 변환
        inc_angle = (-90 - inc_angle) % 360
        inc_angle = inc_angle * np.pi / 180.
        inc_dir_true = np.array([np.cos(inc_angle), np.sin(inc_angle)])
        out_angle = (90 - out_angle) % 360
        out_angle = out_angle * np.pi / 180.
        out_dir_true = np.array([np.cos(out_angle), np.sin(out_angle)])
        # 매칭 엣지 반환
        inc_index = np.array([np.dot(inc_dir, inc_dir_true) for inc_dir in inc_dirs]).argmax()
        out_index = np.array([np.dot(out_dir, out_dir_true) for out_dir in out_dirs]).argmax()
        inc_edge_id = inc_edges[inc_index].getID()
        out_edge_id   = out_edges[out_index].getID()
        match5.at[index, 'inc_edge'] = inc_edge_id
        match5.at[index, 'out_edge'] = out_edge_id
match5['node_id'] = match5['inter_no'].map(inter2node)
match5 = match5[['inter_no', 'node_id', 'move_no', 'inc_edge', 'out_edge']]
match5 = match5.sort_values(by=['inter_no', 'move_no']).reset_index(drop=True)
match5[:60]

inter_no node_id  move_no          inc_edge          out_edge
0        175      i0        1               NaN               NaN
1        175      i0        2      571510153_02      571545870_01
2        175      i0        3     -571542797_02      571510153_01
3        175      i0        4               NaN               NaN
4        175      i0        5      571510153_02      571500487_01
5        175      i0        6               NaN               NaN
6        175      i0        7               NaN               NaN
7        175      i0        8     -571542797_02      571500487_01
8        176      i1        3     -571542810_01      571543469_01
9        176      i1        4   571542797_02.99      571542810_01
10       176      i1        5      571543469_02  -571542797_02.99
11       176      i1        8     -571542810_01  -571542797_02.99
12       176      i1        8     -571542810_01  -571542797_02.99
13       176      i1       18               NaN               NaN
14       177      i2        1               NaN               NaN
15       177      i2        3     -571542809_01      571542809_01
16       177      i2        4               NaN               NaN
17       177      i2        5     -571542809_01      571542811_01
18       177      i2        7               NaN               NaN
19       177      i2        8     -571542809_01      571542811_01
20       177      i2       17               NaN               NaN
21       177      i2       18               NaN               NaN
22       178      i3        1               NaN               NaN
23       178      i3        2   571540303_02.21      571500475_01
24       178      i3        3      571540304_02      571540303_01
25       178      i3        4               NaN               NaN
26       178      i3        5   571540303_02.21      571556450_01
27       178      i3        6               NaN               NaN
28       178      i3        7               NaN               NaN
29       178      i3        8      571540304_02      571556450_01
30       201      i8        1               NaN               NaN
31       201      i8        2      571500618_02      571500617_01
32       201      i8        2      571500618_02      571500617_01
33       201      i8        3     -571500569_01      571500618_01
34       201      i8        4               NaN               NaN
35       201      i8        5      571500618_02      571500583_02
36       201      i8        6               NaN               NaN
37       201      i8        6               NaN               NaN
38       201      i8        7               NaN               NaN
39       201      i8        8     -571500569_01      571500583_02
40       202      i9        2      571510152_01   571510152_01.65
41       202      i9        6               NaN               NaN
42       202      i9       17               NaN               NaN
43       202      i9       18               NaN               NaN
44       206      i7        4               NaN               NaN
45       206      i7        4               NaN               NaN
46       206      i7        8     -571511538_02      571542073_02
47       206      i7        8     -571511538_02      571542073_02
48       206      i7       17               NaN               NaN
49       206      i7       17               NaN               NaN
50       206      i7       18               NaN               NaN
51       206      i7       18               NaN               NaN
52       210      i6        2   571500535_02.18      571542115_01
53       210      i6        3      571500585_02      571500535_01
54       210      i6        4               NaN               NaN
55       210      i6        5   571500535_02.18      571511538_01
56       210      i6        6               NaN               NaN
57       210      i6        7  571511538_02.121      571542115_01
58       210      i6        8      571500585_02      571511538_01
59       210      i6       18               

# 2. 이력 + 이동류

In [25]:
# 5초 단위로 이동류번호 저장 및 신호이력에서 유닉스시각 가져와서 표시, 한시간동안의 데이터만 보관
midnight = int(datetime(2024, 1, 5, 0, 0, 0).timestamp())
next_day = int(datetime(2024, 1, 6, 0, 0, 0).timestamp())
fsecs = range(midnight, next_day, 5) # fsecs : unix time by Five SECondS
fsec2move = dict(zip(fsecs,moves))
history = pd.read_csv('../../Data/tables/history.csv', index_col=0)

fsec2movement = {}
# - 아래 절차를 5초마다 반복
for fsec in tqdm(fsecs): # fsec : unix time by Five SECond
    # 1. 상태 테이블 조회해서 전체 데이터중 필요데이터(교차로번호, A링 현시번호, A링 이동류번호, B링 현시번호, B링 이동류번호)만 수집 : A
    move = fsec2move[fsec]
    # 2. 이력 테이블 조회해서 교차로별로 유닉스시간 최대인 데이터(교차로변호, 종료유닉스타임)만 수집 : B
    recent_histories = [group.iloc[-1:] for _, group in history[history['end_unix'] < fsec].groupby('inter_no')]
    if not recent_histories:
        rhistory = pd.DataFrame({'inter_no':[], 'end_unix':[]}) # recent history
    else:
        rhistory = pd.concat(recent_histories)
    recent_unix = rhistory[['inter_no', 'end_unix']]
    # 3. 상태 테이블 조회정보(A)와 이력 테이블 조회정보(B) 조인(키값 : 교차로번호) : C
    move = pd.merge(move, recent_unix, how='left', left_on='inter_no', right_on='inter_no')
    move['end_unix'] = move['end_unix'].fillna(0).astype(int)
    move = move.drop_duplicates()
    # 4. C데이터 프레임에 신규 컬럼(시작 유닉스타임) 생성 후 종료유닉스 타임 값 입력, 종료 유닉스 타임 컬럼 제거
    move = move.rename(columns = {'end_unix':'start_unix'})
    # 5. 이동류 이력정보 READ
    #     - CSV 파일로 서버에 저장된 이동류정보를 읽어옴(파일이 없는 경우에는 데이터가 없는 프레임 D 생성)
    try:
        if isinstance(movement, pd.DataFrame):
            pass
        else:
            movement = pd.DataFrame()
    except NameError:
        movement = pd.DataFrame()
    # 6. 이동류 이력정보 데이터테이블(D)에 C데이터 add
    movement = pd.concat([movement, move])
    # 7. D데이터 프레임에서 중복데이터 제거(교차로번호, 시작 유닉스타임, A링 현시번호, B링 현시번호 같은 행은 제거)
    movement = movement.drop_duplicates(['inter_no','phas_A','phas_B','start_unix'])
    # 8. D데이터 보관 시간 기준시간을 시작 유닉스 타임의 최대값 - 3600을 값으로 산출하고, 보관 시간 기준시간보다 작은 시작 유닉스 타임을 가진 행은 모두 제거(1시간 데이터만 보관)
    movement = movement[movement.start_unix > fsec - 3600]
    movement = movement.sort_values(by=['start_unix','inter_no','phas_A','phas_B']).reset_index(drop=True)

    fsec2movement[fsec] = movement
    movement.to_csv(f'../../Data/tables/movements/movements_{fsec}.csv')
# del movement

100%|██████████| 17280/17280 [02:21<00:00, 122.48it/s]


In [108]:
fsecs[3]

1704380415

In [26]:
# 세부현시로 되어있던 history를 기존 방식(A, B로 나뉘어 현시시간이 구성된 형태)로 바꿈.
plan = pd.read_csv('../../Data/tables/plan.csv', index_col=0)
history = pd.read_csv('../../Data/tables/history.csv', index_col=0)
splits = {}
for i, row in plan.iterrows():
    inter_no = row.inter_no
    start_hour = row.start_hour
    start_minute = row.start_minute
    splits[(inter_no, start_hour, start_minute)] = {}
    cycle = row.cycle
    cums_A = row[[f'dura_A{j}' for j in range(1,9)]].cumsum()
    cums_B = row[[f'dura_B{j}' for j in range(1,9)]].cumsum()
    split = {}
    k = 0
    for t in range(cycle):
        new_phas_A = len(cums_A[cums_A < t]) + 1
        new_phas_B = len(cums_B[cums_B < t]) + 1
        if k == 0 or ((new_phas_A, new_phas_B) != (phas_A, phas_B)):
            k += 1
        phas_A = new_phas_A
        phas_B = new_phas_B
        splits[(inter_no, start_hour, start_minute)][(phas_A, phas_B)] = k
isplits = {} # the inverse of splits
for i in splits:
    isplits[i] = {splits[i][k]:k for k in splits[i]}
for i, row in history.iterrows():
    inter_no = row.inter_no
    start_hour = row.start_hour
    start_minute = row.start_minute
    split = isplits[(inter_no,start_hour,start_minute)]
    durs = {}
    dur_chars = [f'dur_{alph}{j}' for alph in ['A', 'B'] for j in range(1, 9)]
    for dur_char in dur_chars:
        durs[dur_char] = 0
    for k in range(1, len(split)+1):
        ja = split[k][0]
        jb = split[k][1]
        durs[f'dur_A{ja}'] += row[f'ddur_{k}']
        durs[f'dur_B{jb}'] += row[f'ddur_{k}']
    for dur_char in dur_chars:
        history.at[i, dur_char] = durs[dur_char]
history = history[['inter_no','end_unix'] + dur_chars + ['cycle']].astype(int)
history = history.astype(int).sort_values(by = ['end_unix','inter_no'])
history.head()

inter_no    end_unix  dur_A1  dur_A2  dur_A3  dur_A4  dur_A5  dur_A6  \
0       206  1704380520      33      35      26      26       0       0   
1       211  1704380525      28      97       0       0       0       0   
2       178  1704380540      38      39      40      23       0       0   
3       201  1704380540      24      24      17      58      17       0   
4       202  1704380540      39     101       0       0       0       0   

   dur_A7  dur_A8  dur_B1  dur_B2  dur_B3  dur_B4  dur_B5  dur_B6  dur_B7  \
0       0       0      33      35      26      26       0       0       0   
1       0       0      28      97       0       0       0       0       0   
2       0       0      38      39      40      23       0       0       0   
3       0       0      24      24      17      58      17       0       0   
4       0       0      39     101       0       0       0       0       0   

   dur_B8  cycle  
0       0    120  
1       0    125  
2       0    140  
3       0    140  
4       0    140

In [62]:
# - 5분마다 신호이력 데이터 수집해서 통합테이블 생성할때
fmins = range(midnight, next_day, 300) # fmins : unix time by Five MINuteS
moves_fmins = [pd.read_csv(path_moves + csv_move, index_col=0) for csv_move in csv_moves if int(csv_move[5:-4]) in fmins]
fmin2move = dict(zip(fmins,moves_fmins))
fmin = fmins[60] # ranges from 0 to 288
print(fmin)
# 1. 조회시점의 유닉스 타임을 기준으로 신호이력의 유닉스 타임이 1시간(또는 2시간) 이내인 데이터 수집
rhistory = history.copy()
rhistory = rhistory[(rhistory.end_unix < fmin) & (rhistory.end_unix >= fmin - 3600)]
durs_A = [f'dur_A{j}' for j in range(1, 9)]
durs_B = [f'dur_B{j}' for j in range(1, 9)]
# 2. 시작 유닉스 타임컬럼 생성 후 종류 유닉스 타임에서 현시별 현시기간 컬럼의 합을 뺀 값으로 입력
# - 현시시간의 합을 뺀 시간의 +- 10초 이내에 이전 주기정보가 존재하면 그 유닉스 시간을 시작 유닉스시간 값으로 하고, 존재하지 않으면 현시시간의 합을 뺀 유닉스 시간을 시작 유닉스 시간으로 지정
# # 이전 유닉스 존재하지 않음 => 현시시간 합의 차
# # 이전 유닉스 존재, abs < 10 => 이전 유닉스
# # 이전 유닉스 존재, abs >=10 => 현시시간 합의 차
for i, row in rhistory.iterrows():
    inter_no = row.inter_no
    end_unix = row.end_unix
    elapsed_time = row[durs_A].sum()
    start_unix = end_unix - elapsed_time
    pre_rows = history[:i] # previous rows
    if inter_no in pre_rows.inter_no.unique(): # 이전 유닉스 존재
        pre_unix = pre_rows[pre_rows.inter_no == inter_no]['end_unix'].iloc[-1] # previous unix time
        if abs(pre_unix - start_unix) < 10: # abs < 10
            start_unix = pre_unix
        else: # abs >= 10
            pass
    rhistory.loc[i, 'start_unix'] = start_unix
rhistory[rhistory.isna()] = 0
rhistory['start_unix'] = rhistory['start_unix'].astype(int)
# with pd.option_context('display.max_rows', None, 'display.max_columns', None):
#     display(rhistory)
rhistory = rhistory[['inter_no', 'start_unix'] + dur_chars + ['cycle']]
rhistory

1704398400


inter_no  start_unix  dur_A1  dur_A2  dur_A3  dur_A4  dur_A5  dur_A6  \
562       176  1704394651      37      73      40       0       0       0   
563       175  1704394640      37      39      55      29       0       0   
564       201  1704394680      24      24      17      58      17       0   
565       202  1704394681      39     101       0       0       0       0   
566       178  1704394690      38      39      40      23       0       0   
..        ...         ...     ...     ...     ...     ...     ...     ...   
691       175  1704398160      37      39      55      29       0       0   
692       201  1704398180      24      24      17      58      17       0   
693       202  1704398180      39     101       0       0       0       0   
694       211  1704398245      28      97       0       0       0       0   
695       210  1704398220      43      29      56      22       0       0   

     dur_A7  dur_A8  dur_B1  dur_B2  dur_B3  dur_B4  dur_B5  dur_B6  dur_B7  \
562       0       0      37      73      40       0       0       0       0   
563       0       0      37      39      25      59       0       0       0   
564       0       0      24      24      17      58      17       0       0   
565       0       0      39     101       0       0       0       0       0   
566       0       0      38      39      40      23       0       0       0   
..      ...     ...     ...     ...     ...     ...     ...     ...     ...   
691       0       0      37      39      25      59       0       0       0   
692       0       0      24      24      17      58      17       0       0   
693       0       0      39     101       0       0       0       0       0   
694       0       0      28      97       0       0       0       0       0   
695       0       0      24      48      56      22       0       0       0   

     dur_B8  cycle  
562       0    150  
563       0    160  
564       0    140  
565       0    140  
566       0    140  
..      ...    ...  
691       0    160  
692       0    140  
693       0    140  
694       0    125  
695       0    150  

[134 rows x 19 columns]

In [66]:
splits = {}
for i, row in tqdm(rhistory.iterrows()):
    splits[i] = {}
    row = rhistory.iloc[0]
    cycle = row.cycle
    cums_A = row[durs_A].cumsum()
    cums_B = row[durs_B].cumsum()
    k = 0
    for t in range(cycle):
        new_phas_A = len(cums_A[cums_A < t]) + 1
        new_phas_B = len(cums_B[cums_B < t]) + 1
        if k == 0 or ((new_phas_A, new_phas_B) != (phas_A, phas_B)):
            splits[i][(new_phas_A,new_phas_B)] = 0
        phas_A = new_phas_A
        phas_B = new_phas_B
        k += 1
        splits[i][(phas_A, phas_B)] += 1

134it [00:03, 40.01it/s]


In [88]:
hrhistory = pd.DataFrame({'inter_no':[], 'start_unix':[], 'phas_A':[],'phas_B':[],'duration':[]}) # hierarchied recent history
for i, row in tqdm(rhistory.iterrows()):
    for (phas_A, phas_B) in splits[i].keys():
        new_row = {}
        new_row['inter_no'] = [row.inter_no]
        new_row['start_unix'] = [row.start_unix]
        new_row['phas_A'] = [phas_A]
        new_row['phas_B'] = [phas_B]
        new_row['duration'] = [splits[i][(phas_A, phas_B)]]
        new_row = pd.DataFrame(new_row)
        # display(new_row)
        hrhistory = pd.concat([hrhistory, new_row])
hrhistory = hrhistory.astype(int).sort_values(by=['start_unix', 'inter_no']).reset_index(drop=True)
hrhistory

134it [00:00, 950.49it/s]


inter_no  start_unix  phas_A  phas_B  duration
0         175  1704394640       1       1        38
1         175  1704394640       2       2        73
2         175  1704394640       3       3        39
3         176  1704394651       1       1        38
4         176  1704394651       2       2        73
..        ...         ...     ...     ...       ...
397       210  1704398220       2       2        73
398       210  1704398220       3       3        39
399       211  1704398245       1       1        38
400       211  1704398245       2       2        73
401       211  1704398245       3       3        39

[402 rows x 5 columns]

In [103]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    display(fsec2movement[fmin])

inter_no  phas_A  phas_B  move_A  move_B  start_unix
0         175       1       1       8       4  1704394801
1         175       2       2       7       3  1704394801
2         175       3       3       6       1  1704394801
3         175       3       4       6       2  1704394801
4         175       4       4       5       2  1704394801
5         201       1       1       8       3  1704394820
6         201       2       2       5       2  1704394820
7         201       3       3       6       2  1704394820
8         201       4       4       6       1  1704394820
9         201       5       5       7       4  1704394820
10        202       1       1       6       2  1704394820
11        202       2       2      17      18  1704394820
12        178       1       1       8       4  1704394830
13        178       2       2       7       3  1704394830
14        178       3       3       5       2  1704394830
15        178       4       4       6       1  1704394830
16        176       1       1       8       4  1704394950
17        176       2       2       8       3  1704394950
18        176       3       3       5      18  1704394950
19        175       1       1       8       4  1704394960
20        175       2       2       7       3  1704394960
21        175       3       3       6       1  1704394960
22        175       3       4       6       2  1704394960
23        175       4       4       5       2  1704394960
24        201       1       1       8       3  1704394960
25        201       2       2       5       2  1704394960
26        201       3       3       6       2  1704394960
27        201       4       4       6       1  1704394960
28        201       5       5       7       4  1704394960
29        202       1       1       6       2  1704394961
30        202       2       2      17      18  1704394961
31        178       1       1       8       4  1704394970
32        178       2       2       7       3  1704394970
33        178       3       3       5       2  1704394970
34        178       4       4       6       1  1704394970
35        201       1       1       8       3  1704395100
36        201       2       2       5       2  1704395100
37        201       3       3       6       2  1704395100
38        201       4       4       6       1  1704395100
39        201       5       5       7       4  1704395100
40        202       1       1       6       2  1704395100
41        202       2       2      17      18  1704395100
42        176       1       1       8       4  1704395101
43        176       2       2       8       3  1704395101
44        176       3       3       5      18  1704395101
45        178       1       1       8       4  1704395110
46        178       2       2       7       3  1704395110
47        178       3       3       5       2  1704395110
48        178       4       4       6       1  1704395110
49        175       1       1       8       4  1704395119
50        175       2       2       7       3  1704395119
51        175       3       3       6       1  1704395119
52        175       3       4       6       2  1704395119
53        175       4       4       5       2  1704395119
54        201       1       1       8       3  1704395240
55        201       2       2       5       2  1704395240
56        201       3       3       6       2  1704395240
57        201       4       4       6       1  1704395240
58        201       5       5       7       4  1704395240
59        202       1       1       6       2  1704395240
60        202       2       2      17      18  1704395240
61        176       1       1       8       4  1704395250
62        176       2       2       8       3  1704395250
63        176       3       3       5      18  1704395250
64        177       1       1       8       4  1704395250
65        177       2       2       7       3  1704395250
66        177       3       3      17      18  1704395250
67        177       4       4       5       1  1704395250
68 

In [101]:
X = sorted(hrhistory.start_unix.unique())
Y = sorted(fsec2movement[fmin].start_unix.unique())
print(fmin)
print(min(X), max(X), max(X) - min(X))
print(min(Y), max(Y), max(Y) - min(Y))

1704398400
1704394640 1704398245 3605
1704394801 1704466700 71899


In [12]:
rhistory[['inter_no', 'start_unix'] + dur_chars + ['cycle']]
# dur_chars
# rhistory.columns

inter_no  start_unix  dur_A1  dur_A2  dur_A3  dur_A4  dur_A5  dur_A6  \
562       176  1704394651      37      73      40       0       0       0   
563       175  1704394640      37      39      55      29       0       0   
564       201  1704394680      24      24      17      58      17       0   
565       202  1704394681      39     101       0       0       0       0   
566       178  1704394690      38      39      40      23       0       0   
..        ...         ...     ...     ...     ...     ...     ...     ...   
691       175  1704398160      37      39      55      29       0       0   
692       201  1704398180      24      24      17      58      17       0   
693       202  1704398180      39     101       0       0       0       0   
694       211  1704398245      28      97       0       0       0       0   
695       210  1704398220      43      29      56      22       0       0   

     dur_A7  dur_A8  dur_B1  dur_B2  dur_B3  dur_B4  dur_B5  dur_B6  dur_B7  \
562       0       0      37      73      40       0       0       0       0   
563       0       0      37      39      25      59       0       0       0   
564       0       0      24      24      17      58      17       0       0   
565       0       0      39     101       0       0       0       0       0   
566       0       0      38      39      40      23       0       0       0   
..      ...     ...     ...     ...     ...     ...     ...     ...     ...   
691       0       0      37      39      25      59       0       0       0   
692       0       0      24      24      17      58      17       0       0   
693       0       0      39     101       0       0       0       0       0   
694       0       0      28      97       0       0       0       0       0   
695       0       0      24      48      56      22       0       0       0   

     dur_B8  cycle  
562       0    150  
563       0    160  
564       0    140  
565       0    140  
566       0    140  
..      ...    ...  
691       0    160  
692       0    140  
693       0    140  
694       0    125  
695       0    150  

[134 rows x 19 columns]

In [13]:
history175 = history[history.inter_no==175]
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    display(history175)

inter_no    end_unix  dur_A1  dur_A2  dur_A3  dur_A4  dur_A5  dur_A6  \
8          175  1704380560      37      39      55      29       0       0   
17         175  1704380720      37      39      55      29       0       0   
27         175  1704380880      37      39      55      29       0       0   
37         175  1704381040      37      39      55      29       0       0   
231        175  1704385040      37      39      55      29       0       0   
238        175  1704385200      37      39      55      29       0       0   
246        175  1704385359      37      39      55      29       0       0   
252        175  1704385520      37      39      55      29       0       0   
258        175  1704385681      37      39      55      29       0       0   
264        175  1704385840      37      39      55      29       0       0   
269        175  1704386000      37      39      55      29       0       0   
274        175  1704386160      37      39      55      29       0       0   
278        175  1704386320      37      39      55      29       0       0   
282        175  1704386480      37      39      55      29       0       0   
286        175  1704386640      37      39      55      29       0       0   
290        175  1704386800      37      39      55      29       0       0   
294        175  1704386960      37      39      55      29       0       0   
299        175  1704387120      37      39      55      29       0       0   
304        175  1704387281      37      39      55      29       0       0   
308        175  1704387440      37      39      55      29       0       0   
313        175  1704387600      37      39      55      29       0       0   
317        175  1704387760      37      39      55      29       0       0   
321        175  1704387920      37      39      55      29       0       0   
326        175  1704388080      37      39      55      29       0       0   
332        175  1704388240      37      39      55      29       0       0   
339        175  1704388400      37      39      55      29       0       0   
344        175  1704388560      37      39      55      29       0       0   
349        175  1704388720      37      39      55      29       0       0   
354        175  1704388880      37      39      55      29       0       0   
359        175  1704389040      37      39      55      29       0       0   
364        175  1704389200      37      39      55      29       0       0   
370        175  1704389360      37      39      55      29       0       0   
377        175  1704389519      37      39      55      29       0       0   
382        175  1704389680      37      39      55      29       0       0   
387        175  1704389840      37      39      55      29       0       0   
392        175  1704390000      37      39      55      29       0       0   
398        175  1704390160      37      39      55      29       0       0   
403        175  1704390320      37      39      55      29       0       0   
410        175  1704390481      37      39      55      29       0       0   
416        175  1704390640      37      39      55      29       0       0   
421        175  1704390800      37      39      55      29       0       0   
426        175  1704390960      37      39      55      29       0       0   
431        175  1704391119      37      39      55      29       0       0   
436        175  1704391280      37      39      55      29       0       0   
441        175  1704391440      37      39      55      29       0       0   
446        175  1704391600      37      39      55      29       0       0   
454        175  1704391760      37      39      55      29       0       0   
459        175  1704391919      37      39      55      29       0       0   
464        175  1704392080      37      39      55      29       0       0   
469        175  1704392240      37      39      55      29       0       0   
475        175  1704392400  

In [14]:
pre_unix = 1
fmins = range(midnight, next_day, 300) # fmins : unix time by Five MINuteS
moves_fmins = [pd.read_csv(path_moves + csv_move, index_col=0) for csv_move in csv_moves if int(csv_move[5:-4]) in fmins]
fmin2move = dict(zip(fmins,moves_fmins))
# - 5분마다 신호이력 데이터 수집해서 통합테이블 생성할때
# for fmin in tqdm(fmins): # fsec : unix time by Five SECond
fmin = fmins[2]
# 1. 조회시점의 유닉스 타임을 기준으로 신호이력의 유닉스 타임이 1시간(또는 2시간) 이내인 데이터 수집
rhistory = history.copy() # recent history
rhistory = rhistory[rhistory.end_unix < fmin]
durs_A = [f'dur_A{j}' for j in range(1, 9)]
for i, row in rhistory.iterrows():
    inter_no = row.inter_no
    end_unix = row.end_unix
    elapsed_time = row[durs_A].sum()
    start_unix = end_unix - elapsed_time
    pre_rows = rhistory[:i] # previous rows
    if inter_no in pre_rows.inter_no.unique():
        pre_unix = pre_rows[pre_rows.inter_no == inter_no]['end_unix'].iloc[-1] # previous unix time
        if abs(pre_unix - start_unix) < 10:
            pass
        else:
            start_unix = pre_unix
    rhistory.loc[i, 'start_unix'] = start_unix
    print(inter_no)
    print(end_unix)
    print(elapsed_time)
    print(start_unix)

rhistory['start_unix'] = rhistory['start_unix'].astype(int)
rhistory

206
1704380520
120
1704380400
211
1704380525
125
1704380400
178
1704380540
140
1704380400
201
1704380540
140
1704380400
202
1704380540
140
1704380400
176
1704380549
150
1704380399
177
1704380550
150
1704380400
210
1704380550
150
1704380400
175
1704380560
160
1704380400
206
1704380640
120
1704380520
211
1704380645
125
1704380520
202
1704380679
140
1704380539
178
1704380680
140
1704380540
201
1704380680
140
1704380540
210
1704380699
150
1704380549
176
1704380700
150
1704380550
177
1704380700
150
1704380550
175
1704380720
160
1704380560
206
1704380760
120
1704380640
211
1704380765
125
1704380640
178
1704380820
140
1704380820
201
1704380820
140
1704380680
202
1704380820
140
1704380680
176
1704380850
150
1704380700
177
1704380850
150
1704380700
210
1704380850
150
1704380700
175
1704380880
160
1704380880
206
1704380880
120
1704380760
211
1704380885
125
1704380760
178
1704380960
140
1704380820
201
1704380960
140
1704380820
202
1704380960
140
1704380820


inter_no    end_unix  dur_A1  dur_A2  dur_A3  dur_A4  dur_A5  dur_A6  \
0        206  1704380520      33      35      26      26       0       0   
1        211  1704380525      28      97       0       0       0       0   
2        178  1704380540      38      39      40      23       0       0   
3        201  1704380540      24      24      17      58      17       0   
4        202  1704380540      39     101       0       0       0       0   
5        176  1704380549      37      73      40       0       0       0   
6        177  1704380550      36      20      68      26       0       0   
7        210  1704380550      43      29      56      22       0       0   
8        175  1704380560      37      39      55      29       0       0   
9        206  1704380640      33      35      26      26       0       0   
10       211  1704380645      28      97       0       0       0       0   
11       202  1704380679      39     101       0       0       0       0   
12       178  1704380680      38      39      40      23       0       0   
13       201  1704380680      24      24      17      58      17       0   
14       210  1704380699      43      29      56      22       0       0   
15       176  1704380700      37      73      40       0       0       0   
16       177  1704380700      36      20      68      26       0       0   
17       175  1704380720      37      39      55      29       0       0   
18       206  1704380760      33      35      26      26       0       0   
19       211  1704380765      28      97       0       0       0       0   
21       178  1704380820      38      39      40      23       0       0   
20       201  1704380820      24      24      17      58      17       0   
22       202  1704380820      39     101       0       0       0       0   
23       176  1704380850      37      73      40       0       0       0   
24       177  1704380850      36      20      68      26       0       0   
25       210  1704380850      43      29      56      22       0       0   
27       175  1704380880      37      39      55      29       0       0   
26       206  1704380880      33      35      26      26       0       0   
28       211  1704380885      28      97       0       0       0       0   
29       178  1704380960      38      39      40      23       0       0   
30       201  1704380960      24      24      17      58      17       0   
31       202  1704380960      39     101       0       0       0       0   

    dur_A7  dur_A8  dur_B1  dur_B2  dur_B3  dur_B4  dur_B5  dur_B6  dur_B7  \
0        0       0      33      35      26      26       0       0       0   
1        0       0      28      97       0       0       0       0       0   
2        0       0      38      39      40      23       0       0       0   
3        0       0      24      24      17      58      17       0       0   
4        0       0      39     101       0       0       0       0       0   
5        0       0      37      73      40       0       0       0       0   
6        0       0      36      20      68      26       0       0       0   
7        0       0      24      48      56      22       0       0       0   
8        0       0      37      39      25      59       0       0       0   
9        0       0      33      35      26      26       0       0       0   
10       0       0      28      97       0       0       0       0       0   
11       0       0      39     101       0       0       0       0       0   
12       0       0      38      39      40      23       0       0       0   
13       0       0      24      24      17      58      17       0       0   
14       0       0      24      48      56      22       0       0       0   
15       0       0      37      73      40       0       0       0       0   
16       0       0      36      20      68      26       0       0       0   
17       0       0      37      39      25      59       0       0       0   
18       0   

In [15]:
fmins = range(midnight, next_day, 300) # fmins : unix time by Five MINuteS
moves_fmins = [pd.read_csv(path_moves + csv_move, index_col=0) for csv_move in csv_moves if int(csv_move[5:-4]) in fmins]
fmin2move = dict(zip(fmins,moves_fmins))
# - 5분마다 신호이력 데이터 수집해서 통합테이블 생성할때
# for fmin in tqdm(fmins): # fsec : unix time by Five SECond
fmin = fmins[2]
print(fmin)
# 1. 조회시점의 유닉스 타임을 기준으로 신호이력의 유닉스 타임이 1시간(또는 2시간) 이내인 데이터 수집
rhistory = history.copy()
rhistory = rhistory[rhistory.end_unix < fmin]
dur_chars = [f'dur_{alph}{j}' for alph in ['A', 'B'] for j in range(1, 9)]
# for i, row in rhistory.iterrows():
i = 17
row = rhistory.iloc[i]
inter_no = row.inter_no
elasped_time = row[dur_chars].sum()
start_unix = row.end_unix - elasped_time
pre_rows = rhistory[:i] # previous rows
if inter_no in pre_rows.inter_no.unique():
    pre_unix = pre_rows[pre_rows.inter_no == inter_no]['end_unix'].iloc[-1] # previous unix time
    if abs(pre_unix - start_unix) < 10:
        print('(1)')
        pass
    else:
        print('(2)')
        start_unix = pre_unix
rhistory.loc[i, 'start_unix'] = start_unix
# rhistory[start_unix] = rhistory[start_unix].astype(int)
print(inter_no)
print(elasped_time)
print(start_unix)
rhistory

1704381000
(2)
175
320
1704380560


inter_no    end_unix  dur_A1  dur_A2  dur_A3  dur_A4  dur_A5  dur_A6  \
0        206  1704380520      33      35      26      26       0       0   
1        211  1704380525      28      97       0       0       0       0   
2        178  1704380540      38      39      40      23       0       0   
3        201  1704380540      24      24      17      58      17       0   
4        202  1704380540      39     101       0       0       0       0   
5        176  1704380549      37      73      40       0       0       0   
6        177  1704380550      36      20      68      26       0       0   
7        210  1704380550      43      29      56      22       0       0   
8        175  1704380560      37      39      55      29       0       0   
9        206  1704380640      33      35      26      26       0       0   
10       211  1704380645      28      97       0       0       0       0   
11       202  1704380679      39     101       0       0       0       0   
12       178  1704380680      38      39      40      23       0       0   
13       201  1704380680      24      24      17      58      17       0   
14       210  1704380699      43      29      56      22       0       0   
15       176  1704380700      37      73      40       0       0       0   
16       177  1704380700      36      20      68      26       0       0   
17       175  1704380720      37      39      55      29       0       0   
18       206  1704380760      33      35      26      26       0       0   
19       211  1704380765      28      97       0       0       0       0   
21       178  1704380820      38      39      40      23       0       0   
20       201  1704380820      24      24      17      58      17       0   
22       202  1704380820      39     101       0       0       0       0   
23       176  1704380850      37      73      40       0       0       0   
24       177  1704380850      36      20      68      26       0       0   
25       210  1704380850      43      29      56      22       0       0   
27       175  1704380880      37      39      55      29       0       0   
26       206  1704380880      33      35      26      26       0       0   
28       211  1704380885      28      97       0       0       0       0   
29       178  1704380960      38      39      40      23       0       0   
30       201  1704380960      24      24      17      58      17       0   
31       202  1704380960      39     101       0       0       0       0   

    dur_A7  dur_A8  dur_B1  dur_B2  dur_B3  dur_B4  dur_B5  dur_B6  dur_B7  \
0        0       0      33      35      26      26       0       0       0   
1        0       0      28      97       0       0       0       0       0   
2        0       0      38      39      40      23       0       0       0   
3        0       0      24      24      17      58      17       0       0   
4        0       0      39     101       0       0       0       0       0   
5        0       0      37      73      40       0       0       0       0   
6        0       0      36      20      68      26       0       0       0   
7        0       0      24      48      56      22       0       0       0   
8        0       0      37      39      25      59       0       0       0   
9        0       0      33      35      26      26       0       0       0   
10       0       0      28      97       0       0       0       0       0   
11       0       0      39     101       0       0       0       0       0   
12       0       0      38      39      40      23       0       0       0   
13       0       0      24      24      17      58      17       0       0   
14       0       0      24      48      56      22       0       0       0   
15       0       0      37      73      40       0       0       0       0   
16       0       0      36      20      68      26       0       0       0   
17       0       0      37      39      25      59       0       0       0   
18       0   

# 3. 결측, 이상치 제거

In [16]:
# fsec2movement = {}
# for fsec in tqdm(fsecs): # fsec : unix time by Five SECond
#     # 1. 상태 테이블 조회해서 전체 데이터중 필요데이터(교차로번호, A링 현시번호, A링 이동류번호, B링 현시번호, B링 이동류번호)만 수집 : A
#     move = fsec2move[fsec]
#     # 2. 이력 테이블 조회해서 교차로별로 유닉스시간 최대인 데이터(교차로변호, 종료유닉스타임)만 수집 : B
#     recent_histories = [group.iloc[-1:] for _, group in history[history['end_unix'] < fsec].groupby('inter_no')]
#     if not recent_histories:
#         rhistory = pd.DataFrame({'inter_no':[], 'end_unix':[]})
#     else:
#         rhistory = pd.concat(recent_histories)
#     recent_unix = rhistory[['inter_no', 'end_unix']]
#     # 3. 상태 테이블 조회정보(A)와 이력 테이블 조회정보(B) 조인(키값 : 교차로번호) : C
#     move = pd.merge(move, recent_unix, how='left', left_on='inter_no', right_on='inter_no')
#     move['end_unix'] = move['end_unix'].fillna(0).astype(int)
#     move = move.drop_duplicates()
#     # 4. C데이터 프레임에 신규 컬럼(시작 유닉스타임) 생성 후 종료유닉스 타임 값 입력, 종료 유닉스 타임 컬럼 제거
#     move = move.rename(columns = {'end_unix':'start_unix'})
#     # 5. 이동류 이력정보 READ
#     #     - CSV 파일로 서버에 저장된 이동류정보를 읽어옴(파일이 없는 경우에는 데이터가 없는 프레임 D 생성)
#     try:
#         if isinstance(movement, pd.DataFrame):
#             pass
#         else:
#             movement = pd.DataFrame()
#     except NameError:
#         movement = pd.DataFrame()
#     # 6. 이동류 이력정보 데이터테이블(D)에 C데이터 add
#     movement = pd.concat([movement, move])
#     # 7. D데이터 프레임에서 중복데이터 제거(교차로번호, 시작 유닉스타임, A링 현시번호, B링 현시번호 같은 행은 제거)
#     movement = movement.drop_duplicates(['inter_no','phas_A','phas_B','start_unix'])
#     # 8. D데이터 보관 시간 기준시간을 시작 유닉스 타임의 최대값 - 3600을 값으로 산출하고, 보관 시간 기준시간보다 작은 시작 유닉스 타임을 가진 행은 모두 제거(1시간 데이터만 보관)
#     movement = movement[movement.start_unix > fsec - 3600]
#     movement = movement.sort_values(by=['start_unix','inter_no','phas_A','phas_B']).reset_index(drop=True)

#     fsec2movement[fsec] = movement
#     movement.to_csv(f'../../Data/tables/movements/movements_{fsec}.csv')
# # del movement